### Gradient Boosted Decision Tree Example

#### Data Loading and Preparation

In [1]:
#from modeva.utils.mlflow import clear_mlflow_home
#clear_mlflow_home()

In [2]:
import pandas as pd
from modeva import DataSet # Import Data Processing Library
df = pd.read_csv("credit_default.csv") # Loading data into pd dataframe
ds = DataSet() # Create dataset object holder
ds.load_dataframe(data = df) 
df

✓ Auth code found in local storage.
Authenticating Modeva...
✓ License is active and valid.
✓ Authenticated successfully!


employment  income    dti  score  amount  tenure  emp_length  \
0              0   86379  0.248    670   10666      12         3.1   
1              0   49629  0.255    739   29036      60         5.2   
2              1   56507  0.358    664   14030      48         1.1   
3              0   60016  0.360    743   14430      24         3.5   
4              0   70743  0.274    710    8131      24         3.4   
...          ...     ...    ...    ...     ...     ...         ...   
9995           0   54259  0.351    740   28389      24         6.2   
9996           0   59587  0.262    721   14771      24         1.1   
9997           0   53006  0.319    747   12894      36         5.8   
9998           1   62029  0.315    743   22315      48        13.6   
9999           1   42823  0.291    711   28623      36         7.1   

      delinquencies   savings  utilization  default  
0                 0  19422.14        0.316        1  
1                 3  21660.48        0.324        0  
2                 0  20396.65        0.287        1  
3                 0  18273.35        0.292        0  
4                 2  14379.34        0.208        0  
...             ...       ...          ...      ...  
9995              2  18015.87        0.313        0  
9996              0  21458.63        0.326        0  
9997              2  18770.42        0.305        0  
9998              1  10018.05        0.334        0  
9999              1  19199.29        0.262        0  

[10000 rows x 11 columns]

#### Data Preprocessing

In [3]:
ds.encode_categorical(method="ordinal") # Encoding categorical variables as ordinal
ds.scale_numerical(features=tuple(ds.feature_names_numerical), 
                   method="standardize") # standardized numerical features
ds.set_target('default') # set target
ds.preprocess() # Run pre-processing
ds.set_random_split(test_ratio = 0.2) # Split training and testing

#### Exploratory Data Analysis

In [4]:
result = ds.eda_2d(feature_x="score", feature_y="default")
result.plot(figsize=(5,4))

#### Build GLM and XGBOOST as Initial Models

##### Setup model objects

In [5]:

from modeva.models import MoXGBClassifier             # Import xgboost library
from modeva.models import MoLogisticRegression        # Import GLM librat

# Stup model objects
model_xgb1 = MoXGBClassifier(name = "XGB_model", max_depth=1, n_estimators=500, learning_rate = 0.01) # GAM with xgboost depth-1
model_xgb2 = MoXGBClassifier(name = "XGB_model", max_depth=2, n_estimators=500, learning_rate = 0.01) # GAMI with xgboost depth-2
# for GLM
model_glm = MoLogisticRegression(name="GLM",
                             feature_names=ds.feature_names,
                             feature_types=ds.feature_types)  # GLM Model

##### Train GLM Model

In [6]:
model_glm.fit(ds.train_x, ds.train_y)

MoLogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
                     intercept_scaling=1, l1_ratio=None, max_iter=100,
                     multi_class='deprecated', n_jobs=None, penalty='l2',
                     random_state=None, solver='lbfgs', tol=0.0001, verbose=0,
                     warm_start=False)

In [7]:
# Check logistic regression result
from modeva import TestSuite  # Import evaluation/testing library
ts_glm = TestSuite(ds, model_glm) # store bundle of dataset and model in ts
# View model performance metrics 
results_glm = ts_glm.diagnose_accuracy_table()
results_glm.table

AUC       ACC   F1   LogLoss     Brier
train  0.748676  0.771875  0.0  0.501888  0.165978
test   0.747515  0.778000  0.0  0.495552  0.163194
GAP   -0.001161  0.006125  0.0 -0.006337 -0.002784

In [8]:
# Check feature importance
results_glm = ts_glm.interpret_coef(features=tuple(ds.feature_names))
results_glm.plot(figsize=(5,4))

##### GAM with xgboost depth-1

In [9]:
# train model with input: ds.train_x and target: ds.train_y
model_xgb1.fit(ds.train_x, ds.train_y)


MoXGBClassifier(base_score=None, booster=None, callbacks=None,
                colsample_bylevel=None, colsample_bynode=None,
                colsample_bytree=None, device=None, early_stopping_rounds=None,
                enable_categorical=False, eval_metric=None, feature_types=None,
                gamma=None, grow_policy=None, importance_type=None,
                interaction_constraints=None, learning_rate=0.01, max_bin=None,
                max_cat_threshold=None, max_cat_to_onehot=None,
                max_delta_step=None, max_depth=1, max_leaves=None,
                min_child_weight=None, missing=nan, monotone_constraints=None,
                multi_strategy=None, n_estimators=500, n_jobs=None,
                num_parallel_tree=None, objective='binary:logistic', ...)

In [10]:
# Check Performance of xgboost
from modeva import TestSuite
ts_xgb1 = TestSuite(ds, model_xgb1) # store bundle of dataset and model in ts
# View model performance metrics 
results_xgb1 = ts_xgb1.diagnose_accuracy_table()
results_xgb1.table

AUC       ACC   F1   LogLoss     Brier
train  0.855503  0.783625  0.0  0.393253  0.125283
test   0.852780  0.790500  0.0  0.387901  0.123187
GAP   -0.002723  0.006875  0.0 -0.005352 -0.002096

In [11]:
# Check feature importance
results_xgb1 = ts_xgb1.interpret_fi()
results_xgb1.plot(n_bars=5, figsize=(5,4))

In [12]:
# Check feature effect of most important feature
results_xgb1 = ts_xgb1.interpret_effects(features = "score")
results_xgb1.plot(figsize = (6,4))

#### Fix xgboost model by applying monotonocity constraints

In [13]:
# for xgboost with monotonic constraints
model_xgb1_mono = MoXGBClassifier(name = "XGB_model", max_depth=1, n_estimators=500, learning_rate = 0.01, monotone_constraints="(0, -1, 1, -1, 0, 0, -1, 1, -1, 1)")
# train model with input: ds.train_x and target: ds.train_y
model_xgb1_mono.fit(ds.train_x, ds.train_y)

MoXGBClassifier(base_score=None, booster=None, callbacks=None,
                colsample_bylevel=None, colsample_bynode=None,
                colsample_bytree=None, device=None, early_stopping_rounds=None,
                enable_categorical=False, eval_metric=None, feature_types=None,
                gamma=None, grow_policy=None, importance_type=None,
                interaction_constraints=None, learning_rate=0.01, max_bin=None,
                max_cat_threshold=None, max_cat_to_onehot=None,
                max_delta_step=None, max_depth=1, max_leaves=None,
                min_child_weight=None, missing=nan,
                monotone_constraints='(0, -1, 1, -1, 0, 0, -1, 1, -1, 1)',
                multi_strategy=None, n_estimators=500, n_jobs=None,
                num_parallel_tree=None, objective='binary:logistic', ...)

In [14]:
# Check Performance of xgboost
ts_xgb1_mono = TestSuite(ds, model_xgb1_mono) # store bundle of dataset and model in ts
# View model performance metrics 
results_xgb1_mono = ts_xgb1_mono.diagnose_accuracy_table()
results_xgb1_mono.table

AUC       ACC   F1   LogLoss     Brier
train  0.777047  0.783625  0.0  0.427749  0.141345
test   0.774165  0.790500  0.0  0.420933  0.138620
GAP   -0.002883  0.006875  0.0 -0.006816 -0.002725

In [15]:
# Check feature effect of most important feature
ts_xgb1_mono = TestSuite(ds, model_xgb1_mono) # store bundle of dataset and model in ts
results_xgb1_mono = ts_xgb1_mono.interpret_effects(features = "score")
results_xgb1_mono.plot(figsize = (6,4))

#### GAMI with monotonic xgboost depth-2

In [16]:
# for xgboost with monotonic constraints
model_xgb2_mono = MoXGBClassifier(name = "XGB_model", max_depth=2, n_estimators=500, learning_rate = 0.01, monotone_constraints="(0, -1, 1, -1, 0, 0, -1, 1, -1, 1)")
# train model with input: ds.train_x and target: ds.train_y
model_xgb2_mono.fit(ds.train_x, ds.train_y)

MoXGBClassifier(base_score=None, booster=None, callbacks=None,
                colsample_bylevel=None, colsample_bynode=None,
                colsample_bytree=None, device=None, early_stopping_rounds=None,
                enable_categorical=False, eval_metric=None, feature_types=None,
                gamma=None, grow_policy=None, importance_type=None,
                interaction_constraints=None, learning_rate=0.01, max_bin=None,
                max_cat_threshold=None, max_cat_to_onehot=None,
                max_delta_step=None, max_depth=2, max_leaves=None,
                min_child_weight=None, missing=nan,
                monotone_constraints='(0, -1, 1, -1, 0, 0, -1, 1, -1, 1)',
                multi_strategy=None, n_estimators=500, n_jobs=None,
                num_parallel_tree=None, objective='binary:logistic', ...)

In [17]:
# Check Performance of xgboost
ts_xgb2_mono = TestSuite(ds, model_xgb2_mono) # store bundle of dataset and model in ts
# View model performance metrics 
results_xgb2_mono = ts_xgb2_mono.diagnose_accuracy_table()
results_xgb2_mono.table

AUC       ACC   F1   LogLoss     Brier
train  0.803187  0.783625  0.0  0.406530  0.136005
test   0.800834  0.790500  0.0  0.400333  0.133833
GAP   -0.002353  0.006875  0.0 -0.006197 -0.002172

In [18]:
# Check feature importance
results_xgb2_mono = ts_xgb1.interpret_fi()
results_xgb2_mono.plot(n_bars=5, figsize=(5,4))

In [19]:
# Check feature effect of most important feature
results_xgb2_mono = ts_xgb2_mono.interpret_effects(features = "score")
results_xgb2_mono.plot(figsize = (6,4))

### Optimize monotonic xgboost model

In [20]:
from modeva.models import ModelTuneGridSearch
param_grid = {"n_estimators": [500, 600, 700],
                "learning_rate": [0.01, 0.05, 0.1]}
model = MoXGBClassifier(max_depth = 2, monotone_constraints="(0, -1, 1, -1, 0, 0, -1, 1, -1, 1)", verbose=-1)
hpo = ModelTuneGridSearch(dataset=ds, model=model)
result = hpo.run(param_grid=param_grid, n_jobs = 20,
                 metric=("AUC", "ACC", "LogLoss", "Brier"),
                 cv=5)
result.table


n_estimators  learning_rate       AUC       ACC   LogLoss     Brier  \
2           700           0.01  0.793752  0.782750  0.412466  0.138088   
0           500           0.01  0.793736  0.783625  0.413109  0.138101   
1           600           0.01  0.793632  0.783375  0.412683  0.138098   
3           500           0.05  0.792780  0.774875  0.415216  0.139634   
4           600           0.05  0.792615  0.773500  0.416325  0.140084   
5           700           0.05  0.791924  0.773125  0.417525  0.140541   
6           500           0.10  0.790031  0.773125  0.420980  0.141751   
7           600           0.10  0.789005  0.772000  0.422954  0.142402   
8           700           0.10  0.788105  0.771000  0.424780  0.142996   

   AUC_rank  ACC_rank  LogLoss_rank  Brier_rank      Time  
2         1         3             1           1  1.570604  
0         2         1             3           3  1.296099  
1         3         2             2           2  1.489325  
3         4         4             4           4  1.358316  
4         5         5             5           5  1.032097  
5         6         7             6           6  1.082908  
6         7         6             7           7  0.702534  
7         8         8             8           8  0.800542  
8         9         9             9           9  0.978370

In [21]:
result.plot("parallel", figsize=(8, 6))

In [22]:
model_xgb2_mono_tuned = MoXGBClassifier(**result.value["params"][2],
                               name="XGB-Tuned", max_depth = 2, monotone_constraints="(0, -1, 1, -1, 0, 0, -1, 1, -1, 1)",
                               verbose=-1)
model_xgb2_mono_tuned.fit(ds.train_x, ds.train_y)

MoXGBClassifier(base_score=None, booster=None, callbacks=None,
                colsample_bylevel=None, colsample_bynode=None,
                colsample_bytree=None, device=None, early_stopping_rounds=None,
                enable_categorical=False, eval_metric=None, feature_types=None,
                gamma=None, grow_policy=None, importance_type=None,
                interaction_constraints=None, learning_rate=0.01, max_bin=None,
                max_cat_threshold=None, max_cat_to_onehot=None,
                max_delta_step=None, max_depth=2, max_leaves=None,
                min_child_weight=None, missing=nan,
                monotone_constraints='(0, -1, 1, -1, 0, 0, -1, 1, -1, 1)',
                multi_strategy=None, n_estimators=700, n_jobs=None,
                num_parallel_tree=None, objective='binary:logistic', ...)

In [23]:
# Check Performance of xgboost
ts_xgb2_mono_tuned = TestSuite(ds, model_xgb2_mono_tuned) # store bundle of dataset and model in ts
# View model performance metrics 
results_xgb2_mono_tuned = ts_xgb2_mono_tuned.diagnose_accuracy_table()
results_xgb2_mono_tuned.table

AUC       ACC   F1   LogLoss     Brier
train  0.805599  0.783625  0.0  0.404629  0.135442
test   0.800143  0.790500  0.0  0.400150  0.134097
GAP   -0.005456  0.006875  0.0 -0.004479 -0.001345

In [24]:
results_xgb2_mono_tuned.plot(name=("confusion_matrix", "test"))


In [25]:
# Check feature importance
results_xgb = ts_xgb2_mono_tuned.interpret_ei()
results_xgb.plot(n_bars=10, figsize=(5,4))

In [26]:
# Check feature effect of most important feature
results_xgb2_mono = ts_xgb2_mono_tuned.interpret_effects(features = "score")
results_xgb2_mono.plot(figsize=(5,4))

In [27]:
# Check feature effect of most important feature
results_xgb2_mono = ts_xgb2_mono_tuned.interpret_effects(features = "dti")
results_xgb2_mono.plot(figsize=(5,4))

# Model Testing for Tuned Monotonic XGBOOST

In [28]:
# Check for Model Weakness by Residual Analysis
# The following analysis is done on the residuals 
results_xgb2_mono_res = ts_xgb2_mono_tuned.diagnose_residual_interpret(dataset='test', n_estimators=100, max_depth=2) # train interpretable GBDT model with depth-2
results_xgb2_mono_res.plot("feature_importance", figsize=(5,4)) # plot feature importance

In [29]:
results_xgb2_mono_res.plot("effect_importance", n_bars = 10, figsize=(5,4)) # plot effect importance

In [30]:
ts_residual = results_xgb2_mono_res.value["TestSuite"] # get the testsuite object
ts_residual.interpret_effects("score", dataset="test").plot(figsize=(5,4)) # plot residual effect plot for feature "credit_score"

In [31]:
ts_residual.interpret_effects(features = ("score", "utilization"), dataset="test").plot(figsize=(5,4)) 

In [32]:
# Test Using Random Forest Proximity
results_RF = ts_xgb2_mono_tuned.diagnose_residual_cluster(
   dataset="test", # dataset to use
   response_type="abs_residual", # response type
   metric="Brier", #metric to use
   n_clusters=10, # number of clusters
   cluster_method="pam", # clustering method
   sample_size=2000, # sample size
   rf_n_estimators=100, # number of trees
   rf_max_depth=5, # max depth of trees
)
results_RF.table # table of cluster performance

Brier   Size  abs_residual
0  0.279036  462.0      0.510024
6  0.228360   65.0      0.475613
4  0.243787  162.0      0.464452
2  0.177343  152.0      0.416425
5  0.109447  137.0      0.266380
3  0.131560  174.0      0.261017
8  0.048382  148.0      0.140790
1  0.024410  191.0      0.080410
7  0.031235  206.0      0.067012
9  0.006084  303.0      0.024351

In [33]:
# Show cluster residuals
results_RF.plot("cluster_residual", figsize=(5,4))

In [34]:
# Show cluster performace
results_RF.plot("cluster_performance", figsize=(5,4))

In [35]:
# Check feature importance
results_RF.plot("feature_importance", figsize=(5,4))

In [36]:
# Test Using Random Forest Proximity
results_RF = ts_xgb2_mono_tuned.diagnose_residual_cluster(
   dataset="test", # dataset to use
   response_type="abs_residual", # response type
   metric="AUC", #metric to use
   n_clusters=10, # number of clusters
   cluster_method="pam", # clustering method
   sample_size=2000, # sample size
   rf_n_estimators=100, # number of trees
   rf_max_depth=5, # max depth of trees
)
# Show cluster performace
results_RF.plot("cluster_performance", figsize=(5,4))

In [37]:
# Check data distribution
cluster_id = 0 # cluster id
data_results = ds.data_drift_test(
   **results_RF.value["clusters"][cluster_id]["data_info"], # use the cluster_id
   distance_metric="PSI", # distance metric using PSI
   psi_method="uniform", # psi method using uniform distribution
   psi_bins=10 # psi bins
)
data_results.plot("summary", figsize=(5,4)) # plot summary of data drift test

In [38]:
data_results.plot(name=('density', 'score'), figsize=(5,4)) # plot density plot for feature "credit_score"

In [39]:
data_results.plot(name=('density', 'income'), figsize=(5,4)) # plot density plot for feature "utilization"

In [40]:
data_results.plot(name=('density', 'default'), figsize=(5,4)) # plot density plot for feature "saving"

In [41]:
# Check data distribution
cluster_id = 5 # cluster id
data_results = ds.data_drift_test(
   **results_RF.value["clusters"][cluster_id]["data_info"], # use the cluster_id
   distance_metric="PSI", # distance metric using PSI
   psi_method="uniform", # psi method using uniform distribution
   psi_bins=10 # psi bins
)
data_results.plot("summary", figsize=(5,4)) # plot summary of data drift test

In [42]:
data_results.plot(name=('density', 'score'), figsize=(5,4)) # plot density plot for feature "credit_score"

In [43]:
data_results.plot(name=('density', 'default'), figsize=(5,4)) # plot density plot for feature "saving"

In [44]:
data_results.plot(name=('density', 'utilization'), figsize=(5,4)) # plot density plot for feature "utilization"

In [45]:
alpha = tuple([i/10 for i in range(1, 11)])
results_xgb2_mono = ts_xgb2_mono.diagnose_resilience(method="worst-sample", metric="AUC", 
                                                   alphas = alpha)
results_xgb2_mono.plot(figsize=(5,4))

In [46]:
# resilience assessment using Worst-Sample scenario
data_results = ds.data_drift_test(
   **results_xgb2_mono.value[0.1]["data_info"],
   distance_metric="PSI",
   psi_method="uniform",
   psi_bins=10)
data_results.plot()

In [47]:
# Reliability Check
results_xgb2_mono = ts_xgb2_mono.diagnose_reliability(
    train_dataset="test",
    test_dataset="test",
    test_size=0.5,
    alpha=0.1,
    random_state=0
)
results_xgb2_mono.table

Avg.Width  Avg.Coverage
0       1.25         0.894

In [48]:
results_xgb2_mono = ts_xgb2_mono.diagnose_residual_cluster(
    dataset="test", 
    response_type="pi_width", 
    metric="AUC", 
    n_clusters=10, 
    cluster_method="pam", 
    sample_size=2000, 
    rf_n_estimators=100, 
    rf_max_depth=5,
)
results_xgb2_mono.table 

AUC   Size  pi_width
0  0.596348  210.0  2.000000
4  0.464286   21.0  2.000000
7  0.545455   16.0  1.812500
3  0.750000   33.0  1.121212
5  0.712121   28.0  1.035714
9  0.881631  577.0  1.001733
1  0.695055   54.0  1.000000
2  0.730769   34.0  1.000000
6  0.642857   15.0  1.000000
8  0.785714   12.0  1.000000

In [50]:
# Show cluster residuals
results_xgb2_mono.plot("cluster_residual", figsize=(5,4))

In [51]:
# Check feature importance
results_xgb2_mono.plot("feature_importance", figsize=(5,4))

In [52]:
# Check data distribution
cluster_id = 0 # cluster id
data_results = ds.data_drift_test(
   **results_xgb2_mono.value["clusters"][cluster_id]["data_info"], # use the cluster_id
   distance_metric="PSI", # distance metric using PSI
   psi_method="uniform", # psi method using uniform distribution
   psi_bins=10 # psi bins
)
data_results.plot("summary", figsize=(5,4)) # plot summary of data drift test

In [53]:
data_results.plot(name=('density', 'score'), figsize=(5,4)) # plot density plot for feature "credit_score"

In [54]:
data_results.plot(name=('density', 'dti'), figsize=(5,4)) # plot density plot for feature "credit_score"

In [55]:
# robustness analysis
results = ts_xgb2_mono.diagnose_robustness(
   perturb_features=None,
   noise_levels=(0.1, 0.2, 0.3, 0.4),
   metric="AUC")
results.plot(figsize=(5,4))

In [56]:
# Robustness Check
results = ts_xgb2_mono.diagnose_residual_cluster(
   dataset="test", # dataset
   response_type="abs_residual_perturb", # response type for robustness clustering
   metric="AUC", # metric
   n_clusters=10, # number of clusters
   cluster_method="pam", # clustering method
   sample_size=2000, # sample size
   rf_n_estimators=100, # number of trees
   rf_max_depth=5, # max depth of trees
)
results.table 

AUC   Size  abs_residual_perturb
0  0.530095  326.0              0.526019
8  0.703929  130.0              0.482256
7  0.480226   65.0              0.465481
3  0.563256  158.0              0.456147
2  0.437500  154.0              0.410773
4  0.690235  148.0              0.291972
5  0.673106  152.0              0.284075
1  0.670738  269.0              0.113734
6  0.847240  230.0              0.091947
9  0.958447  368.0              0.031012

In [57]:
# Show cluster residuals
results.plot("cluster_residual", figsize=(5,4))

In [58]:
# Check feature importance
results.plot("feature_importance", figsize=(5,4))

In [60]:
# Check data distribution
cluster_id = 8 # cluster id
data_results = ds.data_drift_test(
   **results_xgb2_mono.value["clusters"][cluster_id]["data_info"], # use the cluster_id
   distance_metric="PSI", # distance metric using PSI
   psi_method="uniform", # psi method using uniform distribution
   psi_bins=10 # psi bins
)
data_results.plot("summary", figsize=(5,4)) # plot summary of data drift test

In [61]:
data_results.plot(name=('density', 'savings'), figsize=(5,4)) # plot density plot for feature "credit_score"

## Apply Mixture of Experts 

In [62]:
# Build Mixture of Experts
from modeva.models import MoMoEClassifier
model_moe = MoMoEClassifier(max_depth=2, n_estimators = 100, learning_rate = 0.1, n_clusters = 2, monotone_constraints=(0, -1, 1, -1, 0, 0, -1, 1, -1, 1))
model_moe.fit(ds.train_x, ds.train_y)

MoMoEClassifier(base_score=None, booster=None, callbacks=None,
                colsample_bylevel=None, colsample_bynode=None,
                colsample_bytree=None, device=None, early_stopping_rounds=None,
                enable_categorical=False, eval_metric=None, feature_types=None,
                gamma=None, grow_policy=None, importance_type=None,
                interaction_constraints=None, learning_rate=0.1, max_bin=None,
                max_cat_threshold=None, max_cat_to_onehot=None,
                max_delta_step=None, max_depth=2, max_leaves=None,
                min_child_weight=None, missing=nan,
                monotone_constraints=(0, -1, 1, -1, 0, 0, -1, 1, -1, 1),
                multi_strategy=None, n_clusters=2, n_estimators=100,
                n_jobs=None, name='MoMoEClassifier', ...)

In [63]:
# Check MoE performance
from modeva import TestSuite
ts_moe = TestSuite(ds, model_moe)
results_moe = ts_moe.diagnose_accuracy_table()
results_moe.table

AUC       ACC        F1   LogLoss     Brier
train  0.891097  0.850875  0.563164  0.331134  0.105056
test   0.873427  0.850000  0.550898  0.342134  0.109663
GAP   -0.017671 -0.000875 -0.012265  0.011000  0.004606

In [ ]:
# Apply HPO
from modeva.models import ModelTuneGridSearch
param_grid = {"n_estimators": [100, 200, 300],
                "learning_rate": [0.01, 0.05, 0.1], "n_clusters": [2, 3]}
model_moe = MoMoEClassifier(max_depth=2, monotone_constraints=(0, -1, 1, -1, 0, 0, -1, 1, -1, 1))
hpo = ModelTuneGridSearch(dataset=ds, model=model_moe)
result_moe_tuned = hpo.run(param_grid=param_grid, n_jobs = 20, 
                 metric=("AUC", "ACC", "LogLoss", "Brier"),
                 cv=5)
result_moe_tuned.table

In [ ]:
model_moe_tuned = MoMoEClassifier(**result_moe_tuned.value["params"][10],
                               name="MoE-Tuned", max_depth = 2, monotone_constraints="(0, -1, 1, -1, 0, 0, -1, 1, -1, 1)",
                               verbose=-1)
model_moe_tuned.fit(ds.train_x, ds.train_y)
model_moe_tuned

In [ ]:
from modeva import TestSuite
ts_moe = TestSuite(ds, model_moe_tuned)
results_moe = ts_moe.diagnose_accuracy_table()
results_moe.table

In [ ]:
# Plot feature importance
results_moe = ts_moe.interpret_fi()
results_moe.plot(figsize=(5,4))

In [ ]:
# Plot credit score effect
results_moe = ts_moe.interpret_effects(features="score")
results_moe.plot(name = "all", figsize=(5,4))

In [ ]:
# Plot employment length effect
results_moe = ts_moe.interpret_effects(features="emp_length")
results_moe.plot(name = "all", figsize=(5,4))

In [ ]:
# Plot debt to income effect
results_moe = ts_moe.interpret_effects(features="dti")
results_moe.plot(name = "all", figsize=(5,4))

In [ ]:
results_moe = ts_moe.interpret_local_moe_weights(sample_index = 10)
results_moe.plot()

In [ ]:
# Test Using Random Forest Proximity
results_RF = ts_moe.diagnose_residual_cluster(
   dataset="test", # dataset to use
   response_type="abs_residual", # response type
   metric="AUC", # metric to use
   n_clusters=10, # number of clusters
   cluster_method="pam", # clustering method
   sample_size=2000, # sample size
   rf_n_estimators=100, # number of trees
   rf_max_depth=5, # max depth of trees
)
results_RF.table # table of cluster performance

In [ ]:
# Show cluster performace
results_RF.plot("cluster_performance", figsize=(5,4))

In [ ]:
# For classification tasks
from modeva.models import MoNeuralTreeClassifier
model_neut = MoNeuralTreeClassifier(name = "NeuralTree", n_estimators=10, nn_max_epochs = 10, 
                                    feature_names = ds.feature_names, mono_increasing_list = tuple(["utilization", "dti", "delinquencies"]),
                                    mono_decreasing_list = tuple(["score", "income", "savings", "emp_length"]))
# train model with input: ds.train_x and target: ds.train_y
model_neut.fit(ds.train_x, ds.train_y)

In [ ]:
# Create a testsuite that bundles dataset and model
from modeva import TestSuite
ts_neut = TestSuite(ds, model_neut) # store bundle of dataset and model in fs
# View model performance metrics
result = ts_neut.diagnose_accuracy_table()
# display the output
result.table

In [ ]:
result = ts_neut.interpret_fi()
result.plot()

In [ ]:
result = ts_neut.interpret_ei()
result.plot()

In [ ]:
result = ts_neut.interpret_effects(features="score")
result.plot()

In [ ]:
result = ts_neut.interpret_effects(features="utilization")
result.plot()

In [ ]:
ts_neut.interpret_effects(features = ("score", "utilization"), dataset="test").plot(figsize=(5,4)) 

In [ ]:
tsc = TestSuite(ds, models=[model_moe_tuned, model_neut, model_xgb_mono_tuned])
results = tsc.compare_residual_cluster(dataset="test")
results.plot("cluster_performance")